In [1]:
!pip install contractions
!pip install num2words
!pip install nltk

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 289.9/289.9 kB 2.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 110.7/110.7 kB 11.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 143.3/143.3 kB 1.3 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for docopt: filename=docopt-0.6.2-py2.py3-none-any.whl size=13706 sha256=47647bbfc83a19c7a08ccc27ee02a9f6b184a8d83c6b5e9a5cd34659be2ad978
  Stored in directory: /root/.cache/pip/wheels/fc/ab/d4/5da2067ac95b36618c629a5f93f809425700506f72c9732fac
Successfully built docopt


In [4]:
import pandas as pd
import re
import nltk
import contractions
import numpy as np
from google.colab import files
from nltk.tokenize import word_tokenize
import nltk
nltk.download('stopwords')
# Downloading NLTK resources if not already downloaded
nltk.download('punkt')
from nltk.corpus import stopwords
from num2words import num2words
from nltk.stem import WordNetLemmatizer
import gdown

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [5]:
# Download the CSV file from Google Drive
file_id = "1rrEJpW5ZTlagOlBPd7HvZw9c9LWmDHAG"
url = f"https://drive.google.com/uc?id={file_id}"
output = "data.csv"  # Choose the desired output file name
gdown.download(url, output, quiet=False)

# Load the CSV file into a DataFrame
df = pd.read_csv(output)
df

Downloading...
From (original): https://drive.google.com/uc?id=1rrEJpW5ZTlagOlBPd7HvZw9c9LWmDHAG
From (redirected): https://drive.google.com/uc?id=1rrEJpW5ZTlagOlBPd7HvZw9c9LWmDHAG&confirm=t&uuid=a285036d-b29f-41d5-bc95-3ccb62616895
To: /content/data.csv
100%|██████████| 2.29G/2.29G [00:28<00:00, 80.9MB/s]
<ipython-input-5-6ee2bcd43dbd>:8: DtypeWarning: Columns (4) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv(output)


PATENT_ID PATENT_DATE  \
0         10000001  2018-06-19   
1         10000002  2018-06-19   
2         10000003  2018-06-19   
3         10000004  2018-06-19   
4         10000005  2018-06-19   
...            ...         ...   
1912414    9999995  2018-06-19   
1912415    9999996  2018-06-19   
1912416    9999997  2018-06-19   
1912417    9999998  2018-06-19   
1912418    9999999  2018-06-19   

                                              PATENT_TITLE  \
0        Injection molding machine and mold thickness c...   
1        Method for manufacturing polymer film and co-e...   
2        Method for producing a container from a thermo...   
3        Process of obtaining a double-oriented film, c...   
4        Article vacuum formation method and vacuum for...   
...                                                    ...   
1912414  Method for producing molded article of fiber-r...   
1912415  Polymer or polymer composite membrane having t...   
1912416  Metal-plastic composite and method for produci...   
1912417  Glass-resin laminate and method for producing ...   
1912418  Injector for plastic material injection moldin...   

                                           PATENT_ABSTRACT DESCRIPTION_TEXT  \
0        The injection molding machine includes a fixed...              NaN   
1        The present invention relates to: a method for...              NaN   
2        The invention relates to a method for producin...              NaN   
3        The present invention relates to provides a do...              NaN   
4        A vacuum forming apparatus is provided that fo...              NaN   
...                                                    ...              ...   
1912414  A method for producing a molded article of a f...              NaN   
1912415  A polymer or polymer composite membrane having...              NaN   
1912416  A metal-plastic composite and method for produ...              NaN   
1912417  A glass/resin laminate (A) including glass pla...              NaN   
1912418  An injector for a plastic material injection m...              NaN   

              WIPO_SECTOR_TITLE  
0        Mechanical engineering  
1        Mechanical engineering  
2        Mechanical engineering  
3        Mechanical engineering  
4        Mechanical engineering  
...                         ...  
1912414  Mechanical engineering  
1912415  Mechanical engineering  
1912416  Mechanical engineering  
1912417  Mechanical engineering  
1912418  Mechanical engineering  

[1912419 rows x 6 columns]

In [9]:
print(df.shape)

(1912419, 6)


In [10]:
# Checking for NaN values or empty strings
na_or_empty = df.isnull() | (df == '')

# Finding rows with NaN values or empty strings in any column
rows_with_na_or_empty = df[na_or_empty.any(axis=1)]

# Listing PATENT_ID and PATENT_TITLE with NaN or empty values
result = rows_with_na_or_empty[['PATENT_ID', 'PATENT_TITLE']]
print(result)

         PATENT_ID                                       PATENT_TITLE
0         10000001  Injection molding machine and mold thickness c...
1         10000002  Method for manufacturing polymer film and co-e...
2         10000003  Method for producing a container from a thermo...
3         10000004  Process of obtaining a double-oriented film, c...
4         10000005  Article vacuum formation method and vacuum for...
...            ...                                                ...
1912414    9999995  Method for producing molded article of fiber-r...
1912415    9999996  Polymer or polymer composite membrane having t...
1912416    9999997  Metal-plastic composite and method for produci...
1912417    9999998  Glass-resin laminate and method for producing ...
1912418    9999999  Injector for plastic material injection moldin...

[1894431 rows x 2 columns]


In [12]:
# Dropping rows with any NaN values or empty strings
df_cleaned = df.dropna().replace('', pd.NA).dropna()

df_cleaned

PATENT_ID PATENT_DATE  \
359677   11540434  2023-01-03   
359678   11540435  2023-01-03   
359679   11540436  2023-01-03   
359680   11540437  2023-01-03   
359681   11540438  2023-01-03   
...           ...         ...   
377660   11617276  2023-03-28   
377661   11617277  2023-03-28   
377662   11617279  2023-03-28   
377663   11617283  2023-03-28   
377664   11617284  2023-03-28   

                                             PATENT_TITLE  \
359677  Curved cultivating disc with a straight cuttin...   
359678                          Split gauge wheel scraper   
359679  Apparatus for dressing surface of grained mate...   
359680        Spraying support system for working machine   
359681  Mulching insert and system for mounting a mulc...   
...                                                   ...   
377660                         Display device for vehicle   
377661                                    Hinge mechanism   
377662                  Brake for an electronic component   
377663  Heat dissipating plate, manufacturing method t...   
377664  Assemblies including heat dispersing elements ...   

                                          PATENT_ABSTRACT  \
359677  A cultivating disc for a tillage implement inc...   
359678  A scraper assembly for a split gauge wheel of ...   
359679  In an apparatus below an uppermost module 7 ha...   
359680  A spraying support system for a working machin...   
359681  A mulching insert for use with a lawn mower ha...   
...                                                   ...   
377660  A display device is configured to be mounted i...   
377661  A hinge mechanism being used for a foldable el...   
377662  An assembly is provided for an electronic syst...   
377663  A heat dissipating plate includes a casing, a ...   
377664  Assemblies include at least one substrate, at ...   

                                         DESCRIPTION_TEXT  \
359677  Repeat use of reference characters in the pres...   
359678  DESCRIPTION\n\nReferring now to the drawings w...   
359679  DETAILED DESCRIPTION\n\nAn apparatus according...   
359680  DESCRIPTION OF THE EMBODIMENTS\n\nThe embodime...   
359681  DETAILED DESCRIPTION\n\nBefore any embodiments...   
...                                                   ...   
377660  DETAILED DESCRIPTION\n\nHereinafter, one or mo...   
377661  DETAILED DESCRIPTION OF THE PREFERRED EMBODIME...   
377662  DETAILED DESCRIPTION\n\nFIG.1illustrates an as...   
377663  DETAILED DESCRIPTION OF THE EMBODIMENT\n\nIt s...   
377664  DETAILED DESCRIPTION\n\nAs used herein, any re...   

             WIPO_SECTOR_TITLE  
359677  Mechanical engineering  
359678  Mechanical engineering  
359679  Mechanical engineering  
359680  Mechanical engineering  
359681  Mechanical engineering  
...                        ...  
377660  Mechanical engineering  
377661  Mechanical engineering  
377662  Mechanical engineering  
377663  Mechanical engineering  
377664  Mechanical engineering  

[17988 rows x 6 columns]

In [13]:
df_cleaned.shape

(17988, 6)

In [15]:
# Resetting the index of df_cleaned
df_cleaned = df_cleaned.reset_index(drop=True)

In [16]:
df_cleaned

PATENT_ID PATENT_DATE  \
0       11540434  2023-01-03   
1       11540435  2023-01-03   
2       11540436  2023-01-03   
3       11540437  2023-01-03   
4       11540438  2023-01-03   
...          ...         ...   
17983   11617276  2023-03-28   
17984   11617277  2023-03-28   
17985   11617279  2023-03-28   
17986   11617283  2023-03-28   
17987   11617284  2023-03-28   

                                            PATENT_TITLE  \
0      Curved cultivating disc with a straight cuttin...   
1                              Split gauge wheel scraper   
2      Apparatus for dressing surface of grained mate...   
3            Spraying support system for working machine   
4      Mulching insert and system for mounting a mulc...   
...                                                  ...   
17983                         Display device for vehicle   
17984                                    Hinge mechanism   
17985                  Brake for an electronic component   
17986  Heat dissipating plate, manufacturing method t...   
17987  Assemblies including heat dispersing elements ...   

                                         PATENT_ABSTRACT  \
0      A cultivating disc for a tillage implement inc...   
1      A scraper assembly for a split gauge wheel of ...   
2      In an apparatus below an uppermost module 7 ha...   
3      A spraying support system for a working machin...   
4      A mulching insert for use with a lawn mower ha...   
...                                                  ...   
17983  A display device is configured to be mounted i...   
17984  A hinge mechanism being used for a foldable el...   
17985  An assembly is provided for an electronic syst...   
17986  A heat dissipating plate includes a casing, a ...   
17987  Assemblies include at least one substrate, at ...   

                                        DESCRIPTION_TEXT  \
0      Repeat use of reference characters in the pres...   
1      DESCRIPTION\n\nReferring now to the drawings w...   
2      DETAILED DESCRIPTION\n\nAn apparatus according...   
3      DESCRIPTION OF THE EMBODIMENTS\n\nThe embodime...   
4      DETAILED DESCRIPTION\n\nBefore any embodiments...   
...                                                  ...   
17983  DETAILED DESCRIPTION\n\nHereinafter, one or mo...   
17984  DETAILED DESCRIPTION OF THE PREFERRED EMBODIME...   
17985  DETAILED DESCRIPTION\n\nFIG.1illustrates an as...   
17986  DETAILED DESCRIPTION OF THE EMBODIMENT\n\nIt s...   
17987  DETAILED DESCRIPTION\n\nAs used herein, any re...   

            WIPO_SECTOR_TITLE  
0      Mechanical engineering  
1      Mechanical engineering  
2      Mechanical engineering  
3      Mechanical engineering  
4      Mechanical engineering  
...                       ...  
17983  Mechanical engineering  
17984  Mechanical engineering  
17985  Mechanical engineering  
17986  Mechanical engineering  
17987  Mechanical engineering  

[17988 rows x 6 columns]

In [34]:
# Filter rows where PATENT_ID is between 11555473 and 11560450 (inclusive)
df_cleaned_subset = df_cleaned[(df_cleaned['PATENT_ID'] >= 11555473) & (df_cleaned['PATENT_ID'] <= 11560450)]

print(df_cleaned_subset)

      PATENT_ID PATENT_DATE  \
4000   11555473  2023-01-17   
4001   11555474  2023-01-17   
4002   11555475  2023-01-17   
4003   11555476  2023-01-17   
4004   11555477  2023-01-17   
...         ...         ...   
4995   11560418  2023-01-24   
4996   11560438  2023-01-24   
4997   11560443  2023-01-24   
4998   11560446  2023-01-24   
4999   11560450  2023-01-24   

                                           PATENT_TITLE  \
4000                             Dual bladder fuel tank   
4001  Pipe section of a common rail line and methods...   
4002                                            Turbine   
4003  Wind turbine blade root attachment system and ...   
4004  Bird or bat detection and identification for w...   
...                                                 ...   
4995  Methods and compositions for modified factor I...   
4996  Porous polymeric cellulose prepared via cellul...   
4997  Grafted polyvinyl alcohol polymer, formulation...   
4998  Polyurethane foam article and m

In [35]:
# Resetting the index of df_cleaned_subset
df_cleaned_subset = df_cleaned_subset.reset_index(drop=True)

In [36]:
df_cleaned_subset

PATENT_ID PATENT_DATE                                       PATENT_TITLE  \
0     11555473  2023-01-17                             Dual bladder fuel tank   
1     11555474  2023-01-17  Pipe section of a common rail line and methods...   
2     11555475  2023-01-17                                            Turbine   
3     11555476  2023-01-17  Wind turbine blade root attachment system and ...   
4     11555477  2023-01-17  Bird or bat detection and identification for w...   
..         ...         ...                                                ...   
995   11560418  2023-01-24  Methods and compositions for modified factor I...   
996   11560438  2023-01-24  Porous polymeric cellulose prepared via cellul...   
997   11560443  2023-01-24  Grafted polyvinyl alcohol polymer, formulation...   
998   11560446  2023-01-24  Polyurethane foam article and method of formin...   
999   11560450  2023-01-24  Aliphatic-aromatic polyester having elevated w...   

                                       PATENT_ABSTRACT  \
0    A fluid tank comprising can include an outer h...   
1    A pipe section of a common rail line is provid...   
2    A turbine rotor assembly including a unitary b...   
3    Devices, systems, and methods of manufacturing...   
4    An automated system for mitigating risk from a...   
..                                                 ...   
995  The present invention provides Factor IX fusio...   
996  The invention relates to porous polymeric cell...   
997  A grafted polyvinyl alcohol polymer includes a...   
998  A polyurethane foam article comprises the reac...   
999  The present invention relates to an aliphatic-...   

                                      DESCRIPTION_TEXT       WIPO_SECTOR_TITLE  
0    DETAILED DESCRIPTION\n\nFIG.1is a schematic il...  Mechanical engineering  
1    DETAILED DESCRIPTION\n\nFIG.1shows a first emb...  Mechanical engineering  
2    DESCRIPTION OF EMBODIMENTS\n\nAccording to a p...  Mechanical engineering  
3    DETAILED DESCRIPTION\n\nModern wind turbine ro...  Mechanical engineering  
4    DETAILED DESCRIPTION\n\nThe following detailed...  Mechanical engineering  
..                                                 ...                     ...  
995  DETAILED DESCRIPTION OF THE INVENTION\n\nUnles...  Mechanical engineering  
996  Various embodiments of the present invention w...  Mechanical engineering  
997  DETAILED DESCRIPTION OF THE PRESENT INVENTION\...  Mechanical engineering  
998  EXAMPLE\n\nExample 1 is described herein. The ...  Mechanical engineering  
999  EXAMPLES\n\nTest Methods\n\nThe viscosity numb...  Mechanical engineering  

[1000 rows x 6 columns]

In [37]:
# Extracting data from three columns
selected_columns = ['PATENT_ID', 'PATENT_TITLE', 'PATENT_DATE', 'PATENT_ABSTRACT', 'DESCRIPTION_TEXT']
extracted_data = df_cleaned_subset[selected_columns]
extracted_data

PATENT_ID                                       PATENT_TITLE PATENT_DATE  \
0     11555473                             Dual bladder fuel tank  2023-01-17   
1     11555474  Pipe section of a common rail line and methods...  2023-01-17   
2     11555475                                            Turbine  2023-01-17   
3     11555476  Wind turbine blade root attachment system and ...  2023-01-17   
4     11555477  Bird or bat detection and identification for w...  2023-01-17   
..         ...                                                ...         ...   
995   11560418  Methods and compositions for modified factor I...  2023-01-24   
996   11560438  Porous polymeric cellulose prepared via cellul...  2023-01-24   
997   11560443  Grafted polyvinyl alcohol polymer, formulation...  2023-01-24   
998   11560446  Polyurethane foam article and method of formin...  2023-01-24   
999   11560450  Aliphatic-aromatic polyester having elevated w...  2023-01-24   

                                       PATENT_ABSTRACT  \
0    A fluid tank comprising can include an outer h...   
1    A pipe section of a common rail line is provid...   
2    A turbine rotor assembly including a unitary b...   
3    Devices, systems, and methods of manufacturing...   
4    An automated system for mitigating risk from a...   
..                                                 ...   
995  The present invention provides Factor IX fusio...   
996  The invention relates to porous polymeric cell...   
997  A grafted polyvinyl alcohol polymer includes a...   
998  A polyurethane foam article comprises the reac...   
999  The present invention relates to an aliphatic-...   

                                      DESCRIPTION_TEXT  
0    DETAILED DESCRIPTION\n\nFIG.1is a schematic il...  
1    DETAILED DESCRIPTION\n\nFIG.1shows a first emb...  
2    DESCRIPTION OF EMBODIMENTS\n\nAccording to a p...  
3    DETAILED DESCRIPTION\n\nModern wind turbine ro...  
4    DETAILED DESCRIPTION\n\nThe following detailed...  
..                                                 ...  
995  DETAILED DESCRIPTION OF THE INVENTION\n\nUnles...  
996  Various embodiments of the present invention w...  
997  DETAILED DESCRIPTION OF THE PRESENT INVENTION\...  
998  EXAMPLE\n\nExample 1 is described herein. The ...  
999  EXAMPLES\n\nTest Methods\n\nThe viscosity numb...  

[1000 rows x 5 columns]

In [38]:
# Converting all values to lowercase
extracted_data = extracted_data.applymap(lambda x: x.lower() if isinstance(x, str) else x)
extracted_data

PATENT_ID                                       PATENT_TITLE PATENT_DATE  \
0     11555473                             dual bladder fuel tank  2023-01-17   
1     11555474  pipe section of a common rail line and methods...  2023-01-17   
2     11555475                                            turbine  2023-01-17   
3     11555476  wind turbine blade root attachment system and ...  2023-01-17   
4     11555477  bird or bat detection and identification for w...  2023-01-17   
..         ...                                                ...         ...   
995   11560418  methods and compositions for modified factor i...  2023-01-24   
996   11560438  porous polymeric cellulose prepared via cellul...  2023-01-24   
997   11560443  grafted polyvinyl alcohol polymer, formulation...  2023-01-24   
998   11560446  polyurethane foam article and method of formin...  2023-01-24   
999   11560450  aliphatic-aromatic polyester having elevated w...  2023-01-24   

                                       PATENT_ABSTRACT  \
0    a fluid tank comprising can include an outer h...   
1    a pipe section of a common rail line is provid...   
2    a turbine rotor assembly including a unitary b...   
3    devices, systems, and methods of manufacturing...   
4    an automated system for mitigating risk from a...   
..                                                 ...   
995  the present invention provides factor ix fusio...   
996  the invention relates to porous polymeric cell...   
997  a grafted polyvinyl alcohol polymer includes a...   
998  a polyurethane foam article comprises the reac...   
999  the present invention relates to an aliphatic-...   

                                      DESCRIPTION_TEXT  
0    detailed description\n\nfig.1is a schematic il...  
1    detailed description\n\nfig.1shows a first emb...  
2    description of embodiments\n\naccording to a p...  
3    detailed description\n\nmodern wind turbine ro...  
4    detailed description\n\nthe following detailed...  
..                                                 ...  
995  detailed description of the invention\n\nunles...  
996  various embodiments of the present invention w...  
997  detailed description of the present invention\...  
998  example\n\nexample 1 is described herein. the ...  
999  examples\n\ntest methods\n\nthe viscosity numb...  

[1000 rows x 5 columns]

In [39]:
# Defining a function to fix contractions in a text and print the changes
def fix_contractions(text):
    original_text = text
    updated_text = contractions.fix(text)
    print("Original text:", original_text)
    print("Updated text:", updated_text)
    return updated_text

In [40]:
# Applying the function to the 'PATENT_TITLE' column
extracted_data['PATENT_TITLE'] = extracted_data['PATENT_TITLE'].apply(fix_contractions)
# Applying the function to the 'PATENT_ABSTRACT' column
extracted_data['PATENT_ABSTRACT'] = extracted_data['PATENT_ABSTRACT'].apply(fix_contractions)
# Applying the function to the 'DESCRIPTION_TEXT' column
extracted_data['DESCRIPTION_TEXT'] = extracted_data['DESCRIPTION_TEXT'].apply(fix_contractions)

Streaming output truncated to the last 5000 lines.
Original text: processing device, and method for controlling processing device
Updated text: processing device, and method for controlling processing device
Original text: pull-type blind fastener with preload performance
Updated text: pull-type blind fastener with preload performance
Original text: system and method for powder manufacturing
Updated text: system and method for powder manufacturing
Original text: hole saw
Updated text: hole saw
Original text: electromechanical shears for vertical cutting
Updated text: electromechanical shears for vertical cutting
Original text: cutting device
Updated text: cutting device
Original text: method and grinding machine for grinding a gear wheel workpiece
Updated text: method and grinding machine for grinding a gear wheel workpiece
Original text: whirling tool
Updated text: whirling tool
Original text: method of repairing a region of a part including a threaded hole
Updated text: method of rep

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Original text: detailed description

various aspects of the disclosed subject matter are now described with reference to the drawings, wherein like reference numerals are used to refer to like elements throughout. in the following description, for purposes of explanation, numerous specific details are set forth in order to provide a thorough understanding of one or more aspects. it may be evident, however, that such aspect(s) may be practiced without these specific details. in other instances, well-known structures and devices are shown in block diagram form in order to facilitate describing one or more aspects.

vehicles can comprise communication features (e.g., communication and/or content presentation devices) that can be utilized to provide information, entertainment, and other services to occupants of a vehicle and/or allow communications between the occupant of a vehicle and other users outside of the vehicle. autonomous and semi-autonomous vehicles are expected to become more p

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Streaming output truncated to the last 5000 lines.
the extension portions436and440can be configured to receive a fastener configured as a set screw460. as shown infig.32, the lower extension portion436can have a round shape, and can receive the head462of the set screw460within a recess defined in the extension portion436. in certain embodiments, the lower extension portion436can include an anti-rotation feature configured as an anti-rotation tab468. the anti-rotation tab468can be configured to prevent detachment of the blade100from the hub assembly due to vibration. with reference tofig.33, the blade100can include a corresponding u-shaped notch or recess160at or near the center of the proximal edge portion of the blade and extending distally from the proximal edge portion.

as shown infig.33, the extension portions434,438can each define a respective opening or slot464,466, and the blade100can include corresponding extension portions or tabs162,164spaced apart from each other along the 

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Original text: detailed description

embodiments of the present disclosure relate generally to systems used for deploying coils of flexible pipe. the coils of pipe may be self-supported, for example, using bands to hold coils together. the coils of pipe may be self-supported, for example, using bands to hold coils together, or the coils of pipe may be supported around a reel (which may be referred to as a reel of pipe). deployment systems according to embodiments of the present disclosure may include an installation trailer that includes a trailer frame, a lifting mechanism coupled to the trailer frame that is configured to raise or lower a coil of pipe or a reel of pipe, a braking mechanism configured to apply pressure to the pipe while the pipe is being deployed by the system, and a hydraulic power unit configured to hydraulically power the system.

embodiments of the present disclosure will be described below with reference to the figures. in one aspect, embodiments disclosed herein

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [41]:
import re
import nltk
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer

# Download required NLTK resources
nltk.download('stopwords')
nltk.download('wordnet')

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


True

In [42]:
def clean_text(text):
    # Remove text starting with "DESCRIPTION OF"
    text = re.sub(r'\bDESCRIPTION\s*OF\b.*?(?=\b(?:DESCRIPTION\s*OF\b|\bFIG\b))', '', text, flags=re.DOTALL)

    # Remove text related to "FIG"
    text = re.sub(r'\bFIGS?\..*?\b', '', text)

    # Remove numbers from phrases like "a gas turbine1" or "a generator9"
    text = re.sub(r'(\b(?:a|an|the)\s*[a-zA-Z]+)\d+(\b)', r'\1\2', text)

    # Separate numbers and words that are joined
    text = re.sub(r'(\d)([a-zA-Z])', r'\1 \2', text)

    # Remove extra whitespaces
    text = re.sub(r'\s+', ' ', text)

    # Remove all numbers
    text = re.sub(r'\d+', '', text)

    # Keep only one period if there are consecutive periods
    text = re.sub(r'\.{2,}', '.', text)

    # Remove stop words
    stop_words = set(stopwords.words('english'))
    text = ' '.join(word for word in text.split() if word.lower() not in stop_words)

    # Lemmatize the tokens
    lemmatizer = WordNetLemmatizer()
    tokens = [lemmatizer.lemmatize(word) for word in text.split()]

    # Join the tokens back into text
    cleaned_text = ' '.join(tokens)

    return cleaned_text.strip()

# Apply the function to the 'PATENT_ABSTRACT' and 'DESCRIPTION_TEXT' columns
extracted_data['PATENT_ABSTRACT'] = extracted_data['PATENT_ABSTRACT'].apply(clean_text)
extracted_data['DESCRIPTION_TEXT'] = extracted_data['DESCRIPTION_TEXT'].apply(clean_text)

# Print the cleaned DataFrame
print(extracted_data['DESCRIPTION_TEXT'][0])

detailed description fig. schematic illustration fluid container. container used store, ship, and/or distribute various fluids. fluid liquids, gases, slurries, combination thereof. fluid include, limited to, fuel (e.g., hydrogen, hydrogen liquid carrier), water, food beverage products, and/or industrial chemicals. applications, fluid recycling desirable. preferably, fluid recycling system provide storage “spent” “used” fluid (e.g., carrier fluid least portion usable component removed) recycled. one option previously used provide second, separate storage tank collection spent carrier. use separate tank container present challenges, including need additional space footprint second container, additional piping fluid transfer structure, additional weight. challenge exacerbated mobile applications, space weight major limiting factors. previously, capturing waste product process later reuse recycle cumbersome due cost additional ‘wasted’ space store onboard additional handling step cost asso

In [43]:
# Creating a new DataFrame with the concatenated text
concatenated_df = pd.DataFrame({
    'PATENT_ID': extracted_data['PATENT_ID'],
    'PATENT_TITLE': extracted_data['PATENT_TITLE'],
    'PATENT_DATE': extracted_data['PATENT_DATE'],
    'Concatenated_Text': extracted_data.apply(lambda row: f"PATENT_TITLE: {row['PATENT_TITLE']},PATENT_DATE: {row['PATENT_DATE']}, PATENT_ABSTRACT: {row['PATENT_ABSTRACT']}, DESCRIPTION_TEXT: {row['DESCRIPTION_TEXT']}", axis=1)
})

# Display the new DataFrame
concatenated_df

PATENT_ID                                       PATENT_TITLE PATENT_DATE  \
0     11555473                             dual bladder fuel tank  2023-01-17   
1     11555474  pipe section of a common rail line and methods...  2023-01-17   
2     11555475                                            turbine  2023-01-17   
3     11555476  wind turbine blade root attachment system and ...  2023-01-17   
4     11555477  bird or bat detection and identification for w...  2023-01-17   
..         ...                                                ...         ...   
995   11560418  methods and compositions for modified factor i...  2023-01-24   
996   11560438  porous polymeric cellulose prepared via cellul...  2023-01-24   
997   11560443  grafted polyvinyl alcohol polymer, formulation...  2023-01-24   
998   11560446  polyurethane foam article and method of formin...  2023-01-24   
999   11560450  aliphatic-aromatic polyester having elevated w...  2023-01-24   

                                     Concatenated_Text  
0    PATENT_TITLE: dual bladder fuel tank,PATENT_DA...  
1    PATENT_TITLE: pipe section of a common rail li...  
2    PATENT_TITLE: turbine,PATENT_DATE: 2023-01-17,...  
3    PATENT_TITLE: wind turbine blade root attachme...  
4    PATENT_TITLE: bird or bat detection and identi...  
..                                                 ...  
995  PATENT_TITLE: methods and compositions for mod...  
996  PATENT_TITLE: porous polymeric cellulose prepa...  
997  PATENT_TITLE: grafted polyvinyl alcohol polyme...  
998  PATENT_TITLE: polyurethane foam article and me...  
999  PATENT_TITLE: aliphatic-aromatic polyester hav...  

[1000 rows x 4 columns]

In [46]:
concatenated_df.to_csv('concatenated_df.csv', index=False)

files.download('concatenated_df.csv')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>